In [5]:
import json
import re
import pandas as pd
from pandas.io.json import json_normalize

pd.set_option('display.max_rows', 200)
pd.set_option('display.max_columns', 110)

In [6]:
def flattenJSON(json_obj):   
    data = json.loads(json_obj)
    
    def flatten_dict(data):
        for k in list(data):
            if isinstance(data[k], dict):
                child = flatten_dict(data[k])
                for k_ in child:
                    data[k + '.' + k_] = re.sub('^u?\'(.*?)\'','\g<1>',child[k_])
                else:
                    del data[k]
        return data
    
    return flatten_dict(data)

In [7]:
def toConvertableJson(s):    
    def _convertableJson(matchObj):
        if matchObj.group(1):
            return '"'
        elif matchObj.group(2):
            return ':"False"'
        elif matchObj.group(3):
            return ':"True"'
    
    d = flattenJSON(s)
    for i,v in enumerate(d):
        if isinstance(d[v], str) and ('{' in d[v]):
            d[v] = json.loads(re.sub('(\')|(: False)|(: True)',_convertableJson, d[v]))
    return flattenJSON(json.dumps(d))

In [8]:
user[user['useful']>1000]

NameError: name 'user' is not defined

### Business

In [9]:
with open('yelp_dataset/business.json') as f:
    data = [toConvertableJson(line) for line in f]
business = pd.DataFrame(data)
#business = business.sample(frac=0.05, replace=False, random_state=1)
business.drop(['hours','attributes'], axis=1, inplace=True) # null

In [10]:
#business[business['categories'].apply(lambda x:'Coffee & Tea' in x if x is not None else False)]

In [11]:
restaurant = business[business['categories'].apply(lambda x:('Restaurants' in x) or (('Bars' in x) and ('Cigar Bars' not in x) and ('Oxygen Bars' not in x)) or ('Food' in x) or ('Coffee & Tea' in x) or ('Fast Food' in x) or ('Burger' in x) or ('Pizza' in x) or ('Sandwiches' in x) or ('Breakfast & Brunch' in x) if x is not None else False)]
restaurant = restaurant[restaurant['city']=='Las Vegas']

#### drop features(core)

In [12]:
for i in restaurant.columns:
    if 'Hair' in i:
        restaurant.drop(restaurant[(restaurant[i]=='False') | (restaurant[i]=='True')]['business_id'].index, axis=0, inplace=True)
        restaurant.drop(columns=i, axis=1, inplace=True)

#### drop features(for training)

In [13]:
for i in restaurant.columns:
    if ('hour' in i) or ('Wheelchair' in i):
        restaurant.drop(columns=i, axis=1, inplace=True)

In [14]:
restaurant[restaurant['categories'].apply(lambda x:('Shoe Stores' in x) )]['categories'].values

array(['Jewelry, Shopping, Flowers & Gifts, Shoe Stores, Fashion, Gift Shops, Food, Souvenir Shops, Toy Stores, Shopping Centers, Beer, Wine & Spirits'],
      dtype=object)

#### check category

(8869, 90)

In [15]:
cat = []
[cat.extend(n.split(',')) for n in restaurant['categories'] if n is not None ]
cat = [n.strip() for n in cat]
cat = [(n, cat.count(n)) for n in set(cat)]
cat.sort(key=lambda e:e[1], reverse=True)
cat

[('Restaurants', 6450),
 ('Food', 3594),
 ('Nightlife', 1623),
 ('Bars', 1542),
 ('Fast Food', 985),
 ('American (Traditional)', 896),
 ('Mexican', 827),
 ('Coffee & Tea', 766),
 ('Sandwiches', 741),
 ('Pizza', 686),
 ('American (New)', 677),
 ('Burgers', 622),
 ('Breakfast & Brunch', 543),
 ('Specialty Food', 541),
 ('Desserts', 481),
 ('Chinese', 475),
 ('Italian', 454),
 ('Event Planning & Services', 444),
 ('Shopping', 434),
 ('Seafood', 398),
 ('Japanese', 392),
 ('Arts & Entertainment', 386),
 ('Lounges', 372),
 ('Grocery', 367),
 ('Convenience Stores', 360),
 ('Bakeries', 351),
 ('Ice Cream & Frozen Yogurt', 337),
 ('Asian Fusion', 328),
 ('Juice Bars & Smoothies', 309),
 ('Beer', 309),
 ('Wine & Spirits', 309),
 ('Sports Bars', 298),
 ('Sushi Bars', 283),
 ('Chicken Wings', 269),
 ('Cafes', 265),
 ('Salad', 259),
 ('Steakhouses', 254),
 ('Barbeque', 246),
 ('Caterers', 216),
 ('Gas Stations', 210),
 ('Cocktail Bars', 209),
 ('Delis', 206),
 ('Automotive', 189),
 ('Pubs', 189),


#### check null

In [16]:
s = pd.DataFrame({'unique_count':restaurant.nunique(),'null_count':restaurant.isnull().sum()})
#s[s['unique_count']==0]
s

unique_count  null_count
address                                             6060           0
attributes.AcceptsInsurance                            2        8854
attributes.AgesAllowed                                 4        8838
attributes.Alcohol                                     4        2888
attributes.Ambience                                    1        8826
attributes.Ambience.casual                             2        3120
attributes.Ambience.classy                             2        3120
attributes.Ambience.divey                              2        3119
attributes.Ambience.hipster                            2        3120
attributes.Ambience.intimate                           2        3120
attributes.Ambience.romantic                           2        3120
attributes.Ambience.touristy                           2        3120
attributes.Ambience.trendy                             2        3120
attributes.Ambience.upscale                            2        3144
attributes.BYOB                                        2        8857
attributes.BYOBCorkage                                 3        8538
attributes.BestNights                                  1        8868
attributes.BestNights.friday                           2        8271
attributes.BestNights.monday                           2        8271
attributes.BestNights.saturday                         2        8271
attributes.BestNights.sunday                           2        8271
attributes.BestNights.thursday                         2        8271
attributes.BestNights.tuesday                          2        8271
attributes.BestNights.wednesday                        2        8271
attributes.BikeParking                                 3        2455
attributes.BusinessAcceptsBitcoin                      2        7943
attributes.BusinessAcceptsCreditCards                  3         461
attributes.BusinessParking                             1        8767
attributes.BusinessParking.garage                      2        1328
attributes.BusinessParking.lot                         2        1328
attributes.BusinessParking.street                      2        1328
attributes.BusinessParking.valet                       2        1328
attributes.BusinessParking.validated                   2        1328
attributes.ByAppointmentOnly                           2        8533
attributes.Caters                                      3        3456
attributes.CoatCheck                                   2        8348
attributes.Corkage                                     2        8654
attributes.DietaryRestrictions                         1        8868
attributes.DietaryRestrictions.dairy-free              2        8864
attributes.DietaryRestrictions.gluten-free             2        8864
attributes.DietaryRestrictions.halal                   1        8864
attributes.DietaryRestrictions.kosher                  1        8864
attributes.DietaryRestrictions.soy-free                1        8864
attributes.DietaryRestrictions.vegan                   2        8864
attributes.DietaryRestrictions.vegetarian              2        8864
attributes.DogsAllowed                                 3        8150
attributes.DriveThru                                   3        8369
attributes.GoodForDancing                              2        8136
attributes.GoodForKids                                 3        2888
attributes.GoodForMeal                                 1        8854
attributes.GoodForMeal.breakfast                       2        5012
attributes.GoodForMeal.brunch                          2        5012
attributes.GoodForMeal.dessert                         2        5012
attributes.GoodForMeal.dinner                          2        5012
attributes.GoodForMeal.latenight                       2        5012
attributes.GoodForMeal.lunch                           2        5012
attributes.HappyHour                                   2        8111
attributes.HasTV                          

In [17]:
restaurant

address  \
17                           1775 E Tropicana Ave, Ste 29   
22                                    6007 Dean Martin Dr   
25                                  6055 E Lake Mead Blvd   
43                                        4190 N Pecos Rd   
75                                6125 Spring Mountain Rd   
101                                    3650 E Flamingo Rd   
111                                      4343 N Rancho Dr   
128                   1990 Village Center Circle, Suite 1   
135                      Artisan Hotel, 1501 W Sahara Ave   
173                                 241 W Charleston Blvd   
174                                 3655 Las Vegas Blvd S   
176                                     2411 W Sahara Ave   
198                                   360 E Tropicana Ave   
206                        3500 Las Vegas Blvd S, Ste E11   
214                             1263 Silverado Ranch Blvd   
216                            3342 E Sandhill Rd, Ste 11   
240                            4012 S Rainbow Blvd, Ste J   
249                             4860 S Eastern Ave, Ste 3   
300                                                         
327                                 3655 S Las Vegas Blvd   
353                            2600 W Sahara Ave, Ste 121   
434                                      3000 Paradise Rd   
437                                   3570 Las Vegas Blvd   
464                                  3035 E Tropicana Ave   
494                                    6720 Sky Pointe Dr   
542                                 3475 Las Vegas Blvd S   
543                               1910 Village Center Cir   
665                               7400 S. Las Vegas Blvd.   
693                                 2535 Las Vegas Blvd S   
702                                  2170 S  Rainbow Blvd   
718                                   7537 S Rainbow Blvd   
755              The Palazzo Hotel, 3325 Las Vegas Blvd S   
772                           9500 S Eastern Ave, Ste 150   
776                                     4105 W Sahara Ave   
788                                    221 N Rampart Blvd   
801                                    2685 S Eastern Ave   
815                        8480 S Las Vegas Blvd, Ste 110   
862                                 6593 Las Vegas Blvd S   
873                                                         
929                                5757 Wayne Newton Blvd   
941                                     5061 E Sahara Ave   
945                             6795 W Flamingo Rd, Ste A   
1077                                 7293 W Sahara, Ste 4   
1087                                 2000 Fashion Show Dr   
1095                          8826 S Eastern Ave, Ste 113   
1127                                   2224 S Nellis Blvd   
1158        ARIA Resort & Casino, 3730 S. Las Vegas Blvd.   
1166                                    7150 S Durango Dr   
1172                                2630 Las Vegas Blvd S   
1208                            7291 S Eastern Ave, Ste A   
1283      Adrenaline Sports Bar & Grill, 3103 N Rancho Dr   
1286                                        4158 Koval Ln   
1320                                  6870 W Cheyenne Ave   
1339               10670 Southern Highlands Pkwy, Ste 103   
1349                               5301 W Charleston Blvd   
1355                             707 Fremont St, Ste 1080   
1359                                  8600 W Cheyenne Ave   
1381                                    3389 S Jones Blvd   
1385                                3755 S Las Vegas Blvd   
1400                                     6451 Boulder Hwy   
1402                             4780 W Harmon Ave, Ste 1   
1403                      7400 Las Vegas Blvd S, Ste K145   
1413                            4480 W Spring Mountain Rd   
1443                             3909 W Sahara Ave, Ste 9   
1469                                    552 N Eastern Ave   
1491                    

In [14]:
restaurant.to_csv('./yelp_dataset/restaurant.csv')

In [15]:
restaurant = pd.read_csv('yelp_dataset/restaurant.csv')

/Users/hayley/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning: Columns (2,15,17,38,68,71,74) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [91]:
#[n for n in restaurant.columns if 'Hair' in n]

In [16]:
for i in restaurant.columns:
    print(restaurant[i].value_counts())

186396    1
71024     1
183675    1
1402      1
171385    1
77175     1
124087    1
50546     1
28015     1
138593    1
172621    1
47014     1
34154     1
40297     1
11623     1
140646    1
13692     1
110285    1
140071    1
128396    1
157070    1
44431     1
13716     1
32149     1
182071    1
31559     1
147964    1
178081    1
46492     1
75166     1
21920     1
184706    1
30116     1
182812    1
54624     1
81173     1
115271    1
118067    1
34098     1
23857     1
164075    1
140083    1
122478    1
81189     1
111964    1
149046    1
68899     1
154913    1
42270     1
64797     1
99610     1
146741    1
105785    1
165832    1
19771     1
30012     1
120128    1
177476    1
130373    1
42310     1
175431    1
123205    1
93519     1
25942     1
126295    1
71000     1
102089    1
183643    1
180442    1
26022     1
169699    1
134557    1
161284    1
183811    1
165378    1
153088    1
46588     1
24057     1
28151     1
137725    1
75254     1
173209    1
116210    1
8753

### Review

In [17]:
with open('yelp_dataset/review.json') as f:
    data = [json.loads(line) for line in f]
review = pd.DataFrame(data)
#review = review.sample(frac=0.05, replace=False, random_state=1)

In [18]:
review

business_id  cool                 date  funny  \
0        ujmEBvifdJM6h6RLv4wQIg     0  2013-05-07 04:34:36      1   
1        NZnhc2sEQy3RmzKTZnqtwQ     0  2017-01-14 21:30:33      0   
2        WTqjgwHlXbSFevF32_DJVw     0  2016-11-09 20:09:03      0   
3        ikCg8xy5JIg_NGPx-MSIDA     0  2018-01-09 20:56:38      0   
4        b1b1eb3uo-w561D0ZfCEiQ     0  2018-01-30 23:07:38      0   
5        eU_713ec6fTGNO4BegRaww     0  2013-01-20 13:25:59      0   
6        3fw2X5bZYeW9xCz_zGhOHg     5  2016-05-07 01:21:02      4   
7        zvO-PJCpNk4fgAVUnExYAA     1  2010-10-05 19:12:35      1   
8        b2jN2mm9Wf3RcrZCgfo1cg     0  2015-01-18 14:04:18      0   
9        oxwGyA17NL6c5t1Etg5WgQ     1  2012-02-29 21:52:43      0   
10       8mIrX_LrOnAqWsB5JrOojQ     0  2011-11-30 02:11:15      0   
11       mRUVMJkUGxrByzMQ2MuOpA     0  2017-12-15 23:27:08      1   
12       FxLfqxdYPA6Z85PFKaqLrg     0  2016-05-07 01:36:53      0   
13       LUN6swQYa4xJKaM_UEUOEw     0  2018-04-27 20:25:26      0   
14       AakkkTuGZA2KBodKi2_u8A     0  2012-07-16 00:37:14      1   
15       YvrylyuWgbP90RgMqZQVnQ     0  2017-04-07 21:27:49      0   
16       NyLYY8q1-H3hfsTwuwLPCg     0  2015-01-03 22:47:34      0   
17       cHdJXLlKNWixBXpDwEGb_A     1  2015-04-01 16:30:00      7   
18       6lj2BJ4tJeu7db5asGHQ4w     0  2017-05-26 01:23:19      0   
19       y-Iw6dZflNix4BdwIyTNGA     0  2014-06-27 21:19:23      0   
20       qx6WhZ42eDKmBchZDax4dQ     0  2017-03-27 01:14:37      0   
21       Mem13A3C202RzT53npn4NA     9  2017-05-13 10:41:43      6   
22       I4Nr-MVc26qWr08-S3Q1ow     0  2016-01-17 05:26:22      0   
23       d_L-rfS1vT3JMzgCUGtiow     0  2016-07-25 03:57:19      0   
24       Sfc8Haz2Yri8Mo1L0E0TsA     0  2012-11-06 03:41:43      0   
25       FQ1wBQb3aNeRMThSQEV0Qg     0  2013-12-07 02:32:45      0   
26       hd5xm20tfSa70-6UqD9-bg     1  2014-08-10 22:07:35      1   
27       Gyrez6K8f1AyR7dzW9fvAw     1  2013-12-28 22:28:08      0   
28       9nTF596jDvBBia2EXXiOOg     0  2014-04-19 15:03:17      0   
29       SNL64axQhCO6Z7ohcWg3wA     0  2017-02-09 03:43:25      0   
30       dm6sO_Y8JdKTE1ZM955yug     0  2014-12-17 19:04:33      0   
31       XTzKRvWciP_BZ9imk8mmPQ     0  2014-06-27 21:32:31      1   
32       CDpoJiqgM04wqQTZ6QkTqQ     0  2015-12-05 02:37:03      0   
33       3JxKzWquEbPC3yPIfoCiLw     0  2016-03-07 01:03:08      0   
34       YSUcHqlKMPHHJ_cTrqtNrA     0  2017-12-29 13:55:19      0   
35       N0apJkxIem2E8irTBRKnHw     0  2015-01-18 15:30:50      0   
36       sMzNLdhJZGzYirIWt-fMAg     0  2015-06-21 00:59:14      0   
37       IMLrj2klosTFvPRLv56cng     1  2014-10-11 03:50:27      1   
38       5OZlLXjU0FXUbrw8Scja6g     0  2018-02-01 19:01:16      0   
39       m7ommfJFalI47UksyX04Iw     1  2014-09-25 08:15:44      2   
40       m7ommfJFalI47UksyX04Iw     0  2014-10-27 04:22:34      0   
41       RbrZJEf8TlnP7RHaKnCtIQ     1  2013-11-14 04:55:17      0   
42       wJj1EwYcXHdvA9zKqmb5hQ     0  2018-10-04 11:20:42      0   
43       jScBTQtdAt-8RshaiBEHgw     1  2018-05-28 20:56:05      0   
44       ujHiaprwCQ5ewziu0Vi9rw     0  2013-12-07 00:14:06      0   
45       6sATfFam9_q9uod0I2aCsg     0  2014-02-05 18:07:17      0   
46       EIL41z-hvVCeYHqfA9PyWQ     1  2017-09-20 15:23:35      0   
47       jzveTy7ogH7cg9axZ78ENg     0  2015-04-01 13:31:35      0   
48       OVTZNSkSfbl3gVB9XQIJfw     0  2010-01-08 04:28:23      0   
49       9MbGG8PxrlpBWVm3QyWy_g     0  2016-09-18 15:19:33      0   
50       FBSWwaE6gR7KAOyG1QhakQ     0  2015-01-03 21:11:31      0   
51       X5uxdU9GHoUAqo2wmbg3OQ     1  2015-11-06 00:02:50      0   
52       rBo_suDMdGmFQ0TtYg3b2Q     0  2014-07-13 16:17:18      0   
53       eoyvbnRYQe-z85e8Rc6vAg     0  2013-08-15 15:00:14      0   
54       5FIOXmUE3qMviX9GafGH-Q     0  2017-10-02 02:28:34      0   
55       hcFSc0OHgZJybnjQBrL_8Q     1  2013-05-07 03:29:21      0   
56       OVTZNSkSfbl3gVB9XQIJfw     0  2014-09-09 19:15:26      0   
57       WsdmzI2gi

In [19]:
#review_restaurant = review[review['business_id'].apply(lambda x:x in list(restaurant['business_id']))]
res_k = restaurant[['business_id']]
review_restaurant = res_k.merge(review, how='left',on='business_id')

In [20]:
review_restaurant.to_csv('./yelp_dataset/review_restaurant.csv')

In [21]:
review_restaurant

business_id  cool                 date  funny  \
0        PZ-LZzSlhSe9utkQYU8pFg     0  2011-06-29 02:55:07      0   
1        PZ-LZzSlhSe9utkQYU8pFg     0  2010-10-06 18:20:13      0   
2        PZ-LZzSlhSe9utkQYU8pFg     0  2010-01-13 00:35:45      0   
3        PZ-LZzSlhSe9utkQYU8pFg     0  2008-08-23 20:30:33      0   
4        PZ-LZzSlhSe9utkQYU8pFg     0  2009-06-01 20:02:55      0   
5        PZ-LZzSlhSe9utkQYU8pFg     0  2010-05-22 16:54:57      0   
6        PZ-LZzSlhSe9utkQYU8pFg     0  2008-09-01 21:55:05      0   
7        PZ-LZzSlhSe9utkQYU8pFg     0  2015-04-03 03:59:34      0   
8        PZ-LZzSlhSe9utkQYU8pFg     0  2011-05-06 03:31:40      0   
9        PZ-LZzSlhSe9utkQYU8pFg     2  2010-08-29 16:19:05      0   
10       PZ-LZzSlhSe9utkQYU8pFg     0  2011-01-16 03:09:05      0   
11       PZ-LZzSlhSe9utkQYU8pFg     0  2011-03-29 00:39:22      1   
12       PZ-LZzSlhSe9utkQYU8pFg     1  2007-08-23 06:01:28      3   
13       PZ-LZzSlhSe9utkQYU8pFg     0  2010-07-20 10:09:55      0   
14       PZ-LZzSlhSe9utkQYU8pFg     1  2016-08-09 19:02:44      0   
15       PZ-LZzSlhSe9utkQYU8pFg     1  2010-03-28 00:36:36      0   
16       PZ-LZzSlhSe9utkQYU8pFg     0  2011-03-30 20:36:07      0   
17       PZ-LZzSlhSe9utkQYU8pFg     0  2009-08-30 07:26:47      0   
18       PZ-LZzSlhSe9utkQYU8pFg     1  2010-01-27 04:17:13      0   
19       PZ-LZzSlhSe9utkQYU8pFg     1  2011-02-27 16:01:22      1   
20       PZ-LZzSlhSe9utkQYU8pFg     0  2010-12-17 20:30:54      0   
21       PZ-LZzSlhSe9utkQYU8pFg     1  2011-06-08 19:55:43      0   
22       PZ-LZzSlhSe9utkQYU8pFg     1  2011-04-01 06:18:12      2   
23       PZ-LZzSlhSe9utkQYU8pFg     0  2009-09-06 05:11:50      2   
24       PZ-LZzSlhSe9utkQYU8pFg     1  2011-07-17 18:39:52      0   
25       PZ-LZzSlhSe9utkQYU8pFg     0  2010-04-05 22:45:35      1   
26       PZ-LZzSlhSe9utkQYU8pFg     0  2011-06-27 15:51:04      0   
27       PZ-LZzSlhSe9utkQYU8pFg     0  2011-03-01 18:39:17      0   
28       PZ-LZzSlhSe9utkQYU8pFg     0  2010-04-27 00:40:09      0   
29       PZ-LZzSlhSe9utkQYU8pFg     1  2007-11-01 00:18:12      0   
30       PZ-LZzSlhSe9utkQYU8pFg     0  2014-03-31 05:57:20      0   
31       PZ-LZzSlhSe9utkQYU8pFg     0  2009-07-23 15:45:59      0   
32       PZ-LZzSlhSe9utkQYU8pFg     0  2010-02-17 23:43:54      0   
33       PZ-LZzSlhSe9utkQYU8pFg     0  2009-04-16 18:05:36      0   
34       PZ-LZzSlhSe9utkQYU8pFg     0  2011-12-13 20:28:35      0   
35       PZ-LZzSlhSe9utkQYU8pFg     0  2011-01-28 00:53:08      0   
36       PZ-LZzSlhSe9utkQYU8pFg     2  2009-07-02 16:43:17      2   
37       PZ-LZzSlhSe9utkQYU8pFg     0  2010-11-18 02:34:38      0   
38       PZ-LZzSlhSe9utkQYU8pFg     0  2010-05-12 05:54:48      1   
39       PZ-LZzSlhSe9utkQYU8pFg     0  2007-11-09 16:13:07      1   
40       PZ-LZzSlhSe9utkQYU8pFg     1  2010-11-21 05:13:50      1   
41       KWywu2tTEPWmR9JnBc0WyQ     1  2017-02-19 09:17:53      0   
42       KWywu2tTEPWmR9JnBc0WyQ     0  2014-05-26 21:42:00      0   
43       KWywu2tTEPWmR9JnBc0WyQ     1  2014-03-14 20:58:58      0   
44       KWywu2tTEPWmR9JnBc0WyQ     0  2015-11-20 05:24:45      1   
45       KWywu2tTEPWmR9JnBc0WyQ     0  2018-03-16 07:47:23      0   
46       KWywu2tTEPWmR9JnBc0WyQ     1  2015-10-24 05:25:31      0   
47       KWywu2tTEPWmR9JnBc0WyQ     0  2014-11-13 21:21:04      0   
48       KWywu2tTEPWmR9JnBc0WyQ     2  2015-10-24 09:05:39      1   
49       KWywu2tTEPWmR9JnBc0WyQ     0  2017-02-20 03:43:52      0   
50       KWywu2tTEPWmR9JnBc0WyQ     0  2017-01-29 06:49:58      0   
51       KWywu2tTEPWmR9JnBc0WyQ     0  2014-07-30 20:34:32      0   
52       KWywu2tTEPWmR9JnBc0WyQ     2  2015-10-24 20:25:13      0   
53       KWywu2tTEPWmR9JnBc0WyQ     4  2013-09-08 19:35:16      7   
54       KWywu2tTEPWmR9JnBc0WyQ     2  2016-05-08 00:17:14      2   
55       KWywu2tTEPWmR9JnBc0WyQ     2  2015-09-12 23:12:09      0   
56       KWywu2tTEPWmR9JnBc0WyQ     0  2014-02-09 23:09:06      0   
57       KWywu2tTE

In [ ]:
review_restaurant

### User

In [22]:
with open('yelp_dataset/user.json') as f:
    data = [json.loads(line) for line in f]
user = pd.DataFrame(data)
#user = user.sample(frac=0.05, replace=False, random_state=1)

In [23]:
user

average_stars  compliment_cool  compliment_cute  compliment_funny  \
0                 4.03                1                0                 1   
1                 3.63                1                0                 1   
2                 3.71                0                0                 0   
3                 4.85                0                0                 0   
4                 4.08               80                0                80   
5                 4.20              483               44               483   
6                 4.39             4991              889              4991   
7                 4.33                0                0                 0   
8                 4.21               95                7                95   
9                 4.53               14                2                14   
10                3.60                5                0                 5   
11                3.48                1                0                 1   
12                3.50                0                0                 0   
13                3.95                4                0                 4   
14                3.90               49               11                49   
15                4.50                0                0                 0   
16                3.79              185               18               185   
17                4.10                1                0                 1   
18                3.58              246               13               246   
19                3.10                0                0                 0   
20                3.89              559               29               559   
21                3.45               64                0                64   
22                4.05                1                1                 1   
23                4.31               23                5                23   
24                3.81               19                0                19   
25                3.57               13                2                13   
26                4.44                0                0                 0   
27                4.16                7                0                 7   
28                3.59               57                3                57   
29                2.00                0                0                 0   
30                2.64                0                0                 0   
31                4.25                0                0                 0   
32                4.02              140                1               140   
33                4.20                0                0                 0   
34                4.06              891               86               891   
35                3.61             2267               18              2267   
36                3.82               16                2                16   
37                4.39               75                6                75   
38                3.95              201                1               201   
39                3.64                4                0                 4   
40                5.00                0                0                 0   
41                4.95                0                0                 0   
42                3.24               22                0                22   
43                4.40                1                0                 1   
44                3.95                3                0                 3   
45                3.21               15                0                15   
46                3.60                6                1                 6   
47                2.43                0                0                 0   
48                3.66              822                9               822   
49                3.91                8                2                 8   
50                4.57         

In [24]:
rev_k = pd.DataFrame({'user_id':review_restaurant['user_id'].unique()})
user_restaurant = rev_k.merge(user, how='left',on='user_id')

In [25]:
user_restaurant

user_id  average_stars  compliment_cool  \
0       -Yz2wIcsdJxUOFMbTgoKQA           3.42                3   
1       jYcf_e5p0UG0S-9gJq_tNA           2.86                0   
2       nQC0JiPIk_jCooRDxpuw5A           3.89                0   
3       Gv_-mtOKhWFtCjn9xFe0SQ           4.05               10   
4       pabMYegF28KjHQ5hybAJ0A           3.80                3   
5       F_N4NyoMJWzBYFspeYfH3A           3.60                2   
6       oGYEaOv0IEUZ6kU3JFe98A           4.07                5   
7       EeKyqz_A6xeQ7ezuloqxyg           3.08                0   
8       ks6vHMFVaPACB18GO7XUig           3.35                0   
9       pngNlr9t4HObDgecGH_jaw           3.73               41   
10      SEYmHinZRVXiOFfqWCkuFA           3.83               13   
11      YMgZqBUAddmFErxLtCfK_w           3.62              165   
12      aKDe5qvoYT_1jdMOalehmQ           3.80               28   
13      rhH1Cqta8lb3n-t0fTRm5w           3.97                1   
14      BDjiEmXljD2ZHT61Iv9rrQ           4.52                4   
15      PFqhDyFta-8imsKa4bK3pQ           3.88                0   
16      98VVHG8CpPDf2zbSHqaB7w           3.87                2   
17      sDFQazfIy2uWvjrIjtlfLw           3.59                1   
18      2i_NkXLyuI_QtDa8FIaI3g           4.12               48   
19      KFWOn7x19RmrO6kzTJYmrQ           4.01               23   
20      NEN5RFpZp7DE6K1PK2KZzg           3.88                7   
21      uUkYprg5GP-ExpexAP2s_g           4.44                3   
22      yi_4YTVS6XL7s5atKPbmpA           3.19               20   
23      imINxn9Q__xZ7VUk3JzX0Q           3.49                2   
24      mPU5Ar0NBOw_d95tIfTM0w           3.90                4   
25      L15JCA18Ib_vMUVJILxiSw           3.58               24   
26      NCNR0M5evdswD5y39-jVNw           4.15                0   
27      fOKiJUKlx95N2RSPPtyr5A           4.46                6   
28      9RkL3lRhtAkPUIVyB8_07Q           3.87                6   
29      owbC7FP8SNAlwv6f9S5Stw           3.44                5   
30      jo8vV5iUZLHp617cTKZ7mA           3.83               35   
31      5mkRo6VhwdYQ0X2qbBFE_Q           3.82                2   
32      HRyFtrmf19GTKEM_kOa2pg           3.45               32   
33      ZVn9FCVshH5yxfEKZKR5AQ           4.60                0   
34      Sv1C8Uly4dO1qtytcGMbyg           3.00                0   
35      AoII0-uM9z0EesGnb9YCjQ           3.83                0   
36      t7LwGCCew0LYbkpjoT_OZw           3.20                1   
37      15TfRqjx-2nW52XC4aSkUA           4.03                1   
38      8sdI6ez5FnEbhOiWSvaLVA           4.09                4   
39      xPySNt9FFPIfE07vcHJxPw           3.92                1   
40      co-GuD549dZTJ6OiJS1Ttw           3.80                0   
41      rzQyl74K5sDLUszXuogEEA           5.00                0   
42      2W12K5kX9uZglNqkJ4NjaQ           3.91                0   
43      p0IderpL5zE4D021CXVxtA           3.48                0   
44      5ziFur72HgbuvfaSXASdPQ           5.00                0   
45      iqXtduiWnTPW9A90mocp5Q           5.00                0   
46      wqRcCohnU8tXl91RySQFnQ           3.00                0   
47      eojKDDLxoB4aLw0AZdVKlg           4.33                0   
48      nWAsg9LsVpG7SSNz7vbqJA           2.90                0   
49      IbBze7C6KylGCdCDb7U9FA           1.00                0   
50      9nw8X4eYw1QlP55wAj8sIA           3.63                0   
51      cpoJZ8_c43W22pWHCNPCoA           4.56                0   
52      N4boE_V9Di5efdvJw5K3YQ           4.29                0   
53      iFnkxWfuAmvIeV8DoehLkw           3.14                1   
54      IildZ_8utjDm-0VE94_xbw           3.66                1   
55      xcBFJitTvDYPt7pO-aNTrg           1.00                0   
56      jF9z0D-WPrAPs1ItJm5d5g           5.00                0   
57      zTykmNRo_P3vhpLoY0KaXA           4.00                0   
58      w6u_2e2zj0-ALPL19_eopw           2.62                0   
59      ji-u5dDGTDVdq3Hsrg5QYw           3.72                1 

#### NLP

In [26]:
import nltk
from gensim.models.word2vec import Word2Vec
import string

In [27]:
#stopword 목록 다운로드
nltk.download('stopwords')
stop_words = set(nltk.corpus.stopwords.words('english'))

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/hayley/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [112]:
translator = str.maketrans('', '', string.punctuation)

In [118]:
review_restaurant['text'] = review_restaurant['text'].astype(str)

In [119]:
# each.translate(translator) == 특수문자 제거
# x.lower() == 소문자화
# if x.lower() not in stop_words == 불용어제거
clean = [[x.lower() for x in each.translate(translator).split() if x.lower() not in stop_words] for each in review_restaurant['text'].values]

In [123]:
clean

[['girlfriend',
  'went',
  'dinner',
  'emerald',
  'chinese',
  'thursday',
  'night',
  'workout',
  'arrived',
  'around',
  '730pm',
  'seated',
  'short',
  'wait',
  'browsing',
  'menu',
  'brief',
  'discussion',
  'waiter',
  'ordered',
  'seafood',
  'noodles',
  '3',
  'item',
  'mix',
  'meat',
  'plate',
  'bbq',
  'pork',
  'chicken',
  'duck',
  'food',
  'came',
  'soon',
  'thereafter',
  'hot',
  'delicious',
  'large',
  'portions',
  'lots',
  'seafood',
  'seafood',
  'noodles',
  'mix',
  'meat',
  'plate',
  'came',
  'good',
  'cuts',
  'meat',
  'correct',
  'sauces',
  'meal',
  'received',
  'fortune',
  'cookies',
  'dessert',
  'food',
  'food',
  'good',
  'quality',
  'ingredients',
  'tasted',
  'fresh',
  'dishes',
  'tasted',
  'well',
  'made',
  'food',
  'average',
  'nothing',
  'stood',
  'even',
  'though',
  'quite',
  'hungry',
  'price',
  'price',
  'high',
  'comparative',
  'chinese',
  'cuisine',
  'comparable',
  'large',
  'western',
  

In [171]:
#### it takes too long.

# model = Word2Vec(clean,window=5,min_count=100,sg=1,iter=1000)

# print(list(model.wv.vocab.keys()))
# print("vocab length : %d"%len(model.wv.vocab))

In [170]:
review_restaurant['text'].map(lambda x : len(x.split(' '))).describe()

count    1.386324e+06
mean     1.123440e+02
std      1.075050e+02
min      1.000000e+00
25%      4.200000e+01
50%      7.800000e+01
75%      1.440000e+02
max      1.702000e+03
Name: text, dtype: float64

In [176]:
review_restaurant

business_id               review_id  \
0        PZ-LZzSlhSe9utkQYU8pFg  klcF45wKIOpJW_BhJslOJg   
1        PZ-LZzSlhSe9utkQYU8pFg  Li-pQG6A7p5gbgZHTMeDSQ   
2        PZ-LZzSlhSe9utkQYU8pFg  iRLX3dJ3ONvncIxPnXy1cw   
3        PZ-LZzSlhSe9utkQYU8pFg  rklteWf9xnTU3fAtMFBRRw   
4        PZ-LZzSlhSe9utkQYU8pFg  UfRqM0RGdZa86hFcFEAnjw   
...                         ...                     ...   
1386319  vIAEWbTJc657yN8I4z7whQ  -SEmE5vSGN8VDUF18JRczA   
1386320  vIAEWbTJc657yN8I4z7whQ  -sx8tpdUukgvh0uByg4DBQ   
1386321  vIAEWbTJc657yN8I4z7whQ  82qiOWCRRPTjRcxcIq018g   
1386322  vIAEWbTJc657yN8I4z7whQ  4U49OBNRHvjm62hcBEKy2A   
1386323  vIAEWbTJc657yN8I4z7whQ  9Ofhca869AciZjaEdIGCng   

                        user_id  stars  useful  funny  cool  \
0        -Yz2wIcsdJxUOFMbTgoKQA    5.0       1      0     0   
1        jYcf_e5p0UG0S-9gJq_tNA    4.0       1      0     0   
2        nQC0JiPIk_jCooRDxpuw5A    5.0       1      0     0   
3        Gv_-mtOKhWFtCjn9xFe0SQ    3.0       1      0     0   
4        pabMYegF28KjHQ5hybAJ0A    3.0       1      0     0   
...                         ...    ...     ...    ...   ...   
1386319  8QKrhvVqhEkD8xo4E4s0GQ    5.0       1      0     2   
1386320  9ks-80ZxeCZWNObzEbW4-Q    1.0       3      4     1   
1386321  EA-UgJmd-hQ8RBn1odmDJg    3.0       0      0     0   
1386322  bcxc4OF5SDiJ4xnNMBZUQQ    5.0       0      0     0   
1386323  TglAI9psHTtSRoI7TbttcQ    5.0       3      0     1   

                                                      text  \
0        We went there for dinner the other night, bein...   
1        i had the best Chicken Marcela ever. The spagh...   
2        Basically the best Italian in town for the pri...   
3        Mmmmm delicious food and a little history. Mr....   
4        This is old Vegas, this atmosphere is old scho...   
...                                                    ...   
1386319  The Baristas rock here! I stop in on my way to...   
1386320  This is THE worst Starbucks I've ever been to....   
1386321  The guy here at window just turned this whole ...   
1386322  I honestly don't know why this location has su...   
1386323  This is my favorite starbucks in Las Vegas. I ...   

                        date  
0        2011-06-29 02:55:07  
1        2010-10-06 18:20:13  
2        2010-01-13 00:35:45  
3        2008-08-23 20:30:33  
4        2009-06-01 20:02:55  
...                      ...  
1386319  2012-10-05 22:04:07  
1386320  2015-04-01 04:34:41  
1386321  2015-03-31 21:08:21  
1386322  2017-12-28 06:26:37  
1386323  2013-02-20 03:02:14  

[1386324 rows x 9 columns]

In [177]:
review_txt = review_restaurant['text'].to_list()
review_label = review_restaurant['business_id'].to_list()

#### tokenize

In [ ]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import numpy as np

maxlen = 100  # We will cut reviews after 100 words
training_samples = 20000  # We will be training on 20000 samples
validation_samples = 5000  # We will be validating on 5000 samples
max_words = 10000  # We will only consider the top 10,000 words in the dataset

tokenizer = Tokenizer(num_words=max_words)
tokenizer.fit_on_texts(texts)
# Sequence of all the training samples, with word indexing replacing the actual word.
sequences = tokenizer.texts_to_sequences(texts)
print(sequences[0])

# A sorted dictionary that saves the index of each word, from the most frequent to the least frequent
word_index = tokenizer.word_index
print('Found %s unique tokens.' % len(word_index))

data = pad_sequences(sequences, maxlen=maxlen)
print(data[0])

### Check in

In [12]:
with open('yelp_dataset/checkin.json') as f:
    data = [json.loads(line) for line in f]
checkin = pd.DataFrame(data)
#checkin = checkin.sample(frac=0.05, replace=False, random_state=1)
checkin

business_id  \
0       --1UhMGODdWsrMastO9DZw   
1       --6MefnULPED_I942VcFNA   
2       --7zmmkVg-IMGaXbuVd0SQ   
3       --8LPVSo5i0Oo61X01sV9A   
4       --9QQLMTbFzLJ_oT-ON3Xw   
...                        ...   
161945  zzvlwkcNR1CCqOPXwuvz2A   
161946  zzwaS0xn1MVEPEf0hNLjew   
161947  zzwhN7x37nyjP0ZM8oiHmw   
161948  zzwicjPC9g246MK2M1ZFBA   
161949  zzzaIBwimxVej4tY6qFOUQ   

                                                     date  
0       2016-04-26 19:49:16, 2016-08-30 18:36:57, 2016...  
1       2011-06-04 18:22:23, 2011-07-23 23:51:33, 2012...  
2       2014-12-29 19:25:50, 2015-01-17 01:49:14, 2015...  
3                                     2016-07-08 16:43:30  
4       2010-06-26 17:39:07, 2010-08-01 20:06:21, 2010...  
...                                                   ...  
161945  2017-05-06 20:05:15, 2017-05-12 22:37:03, 2017...  
161946  2010-02-16 02:09:56, 2010-07-05 05:40:48, 2010...  
161947  2016-03-06 13:27:02, 2016-03-09 00:41:53, 2016...  
161948  2012-09-22 00:26:15, 2012-09-23 20:12:00, 2012...  
161949  2012-10-12 16:26:35, 2012-10-19 19:31:14, 2012...  

[161950 rows x 2 columns]

### Tip (not use)

In [13]:
with open('yelp_dataset/tip.json') as f:
    data = [json.loads(line) for line in f]
tip = pd.DataFrame(data)
#tip = tip.sample(frac=0.05, replace=False, random_state=1)
tip

user_id             business_id  \
0        UPw5DWs_b-e2JRBS-t37Ag  VaKXUpmWTTWDKbpJ3aQdMw   
1        Ocha4kZBHb4JK0lOWvE0sg  OPiPeoJiv92rENwbq76orA   
2        jRyO2V1pA4CdVVqCIOPc1Q  5KheTjYPu1HcQzQFtm4_vw   
3        FuTJWFYm4UKqewaosss1KA  TkoyGi8J7YFjA6SbaRzrxg   
4        LUlKtaM3nXd-E4N4uOk_fQ  AkL6Ous6A1atZejfZXn1Bg   
...                         ...                     ...   
1223089  nus5X9JKgU_SzfAL4vhJrg  qdwwiRKwnhdlr9QcgJuzbg   
1223090  95wqYGU6-OiHqRPZP0uAWw  wrs4Zbz17q_G49AIRxRPVw   
1223091  HtLaONYabidSxMS1eGHcXA  wEc4JE2NYQr1RnGjGr4q7w   
1223092  T4R5ZKfcGt1GIAgjCh67eA  n5Hc_iMVkyxcS0SXiBCbOQ   
1223093  2Ag223bd4OtQOnc-F067rQ  wEoaR5WKNtLOLyR1z0TYdg   

                                                      text  \
0        Great for watching games, ufc, and whatever el...   
1        Happy Hour 2-4 daily with 1/2 price drinks and...   
2        Good chips and salsa. Loud at times. Good serv...   
3        The setting and decoration here is amazing. Co...   
4        Molly is definately taking a picture with Sant...   
...                                                    ...   
1223089                Very good class, great instructor!!   
1223090                                     Excellent food   
1223091     Jess is the best bartender!! Go check her out!   
1223092  Excellent food and AMAZING service by Anneliese!!   
1223093                                         Funnnnn!!!   

                        date  compliment_count  
0        2014-03-27 03:51:24                 0  
1        2013-05-25 06:00:56                 0  
2        2011-12-26 01:46:17                 0  
3        2014-03-23 21:32:49                 0  
4        2012-10-06 00:19:27                 0  
...                      ...               ...  
1223089  2018-08-05 20:58:09                 0  
1223090  2018-08-15 18:05:22                 0  
1223091  2018-10-02 03:34:58                 0  
1223092  2018-10-13 16:57:50                 0  
1223093  2018-11-10 03:17:18                 0  

[1223094 rows x 5 columns]

In [ ]:
rev_train

#### EDIT ########## 

In [20]:
restaurant = pd.read_csv('yelp_dataset/restaurant.csv')
restaurant

Unnamed: 0                                            address  \
0             17                       1775 E Tropicana Ave, Ste 29   
1             22                                6007 Dean Martin Dr   
2             25                              6055 E Lake Mead Blvd   
3             43                                    4190 N Pecos Rd   
4             75                            6125 Spring Mountain Rd   
5            101                                 3650 E Flamingo Rd   
6            111                                   4343 N Rancho Dr   
7            128                1990 Village Center Circle, Suite 1   
8            135                   Artisan Hotel, 1501 W Sahara Ave   
9            173                              241 W Charleston Blvd   
10           174                              3655 Las Vegas Blvd S   
11           176                                  2411 W Sahara Ave   
12           198                                360 E Tropicana Ave   
13           206                     3500 Las Vegas Blvd S, Ste E11   
14           214                          1263 Silverado Ranch Blvd   
15           216                         3342 E Sandhill Rd, Ste 11   
16           240                         4012 S Rainbow Blvd, Ste J   
17           249                          4860 S Eastern Ave, Ste 3   
18           300                                                NaN   
19           327                              3655 S Las Vegas Blvd   
20           353                         2600 W Sahara Ave, Ste 121   
21           434                                   3000 Paradise Rd   
22           437                                3570 Las Vegas Blvd   
23           464                               3035 E Tropicana Ave   
24           494                                 6720 Sky Pointe Dr   
25           542                              3475 Las Vegas Blvd S   
26           543                            1910 Village Center Cir   
27           665                            7400 S. Las Vegas Blvd.   
28           693                              2535 Las Vegas Blvd S   
29           702                               2170 S  Rainbow Blvd   
30           718                                7537 S Rainbow Blvd   
31           755           The Palazzo Hotel, 3325 Las Vegas Blvd S   
32           772                        9500 S Eastern Ave, Ste 150   
33           776                                  4105 W Sahara Ave   
34           788                                 221 N Rampart Blvd   
35           801                                 2685 S Eastern Ave   
36           815                     8480 S Las Vegas Blvd, Ste 110   
37           862                              6593 Las Vegas Blvd S   
38           873                                                NaN   
39           929                             5757 Wayne Newton Blvd   
40           941                                  5061 E Sahara Ave   
41           945                          6795 W Flamingo Rd, Ste A   
42          1077                               7293 W Sahara, Ste 4   
43          1087                               2000 Fashion Show Dr   
44          1095                        8826 S Eastern Ave, Ste 113   
45          1127                                 2224 S Nellis Blvd   
46          1158      ARIA Resort & Casino, 3730 S. Las Vegas Blvd.   
47          1166                                  7150 S Durango Dr   
48          1172                              2630 Las Vegas Blvd S   
49          1208                          7291 S Eastern Ave, Ste A   
50          1283    Adrenaline Sports Bar & Grill, 3103 N Rancho Dr   
51          1286                                      4158 Koval Ln   
52          1320                                6870 W Cheyenne Ave   
53          1339             10670 Southern Highlands Pkwy, Ste 103   
54          1349                             5301 W Charleston Blvd   
55          1355              

In [29]:
## cut restaurant id, stars 
df_edit_restaurant = restaurant[["business_id","stars"]]
df_edit_restaurant.rename(columns ={"stars": "biz_stars"}, inplace = True) 
df_edit_restaurant

business_id  biz_stars
0     PZ-LZzSlhSe9utkQYU8pFg        4.0
1     KWywu2tTEPWmR9JnBc0WyQ        4.0
2     tstimHoMcYbkSC4eBA1wEg        4.5
3     NBn4hgfGtNz91k3VsDZlmw        5.0
4     kANF0dbeoW34s2vwh6Umfw        2.0
5     YK5eFV8uS1bCmp8GeiQ-Qg        4.0
6     X8mtoSxY8whtmbDlj0D3Aw        2.0
7     sKhDrZFCJqfRNylkHrIDsQ        4.0
8     bJP4l_BGq2CudEu0m-wNjg        2.0
9     v7ZFEEqJBg_r8NCwHRP_2A        4.5
10    6fPQJq4f_yiq1NHn0fd11Q        3.5
11    k-dDZvTeLysoJvjHI-qr9g        3.0
12    4n81G-pmC3rfhmaPsbwYKg        4.5
13    PWjgwphd2prhtqTPWwLbXw        3.5
14    eY98EH_PHGnJVaJ7t2UpoQ        4.0
15    iwGhazq9eP51PSerTrMrwg        4.0
16    0G83H_zoum-Q4bWU2olTqQ        4.5
17    IjGU7ZopsgeomsDQf20UXQ        4.0
18    XWa7nXOddOYKxojywngk8w        5.0
19    ci3xUs8ZffvGhWfoioAL0Q        3.5
20    xXtWrRKn8A708BfaNs1nZw        4.0
21    wdsGP5rJinx0J5GcGzPQUw        4.0
22    SZ5KO1KNiwtrktKo5mpuLA        3.5
23    LEOvXK3lMEfjnex3CPvrng        4.5
24    k2b3niokS_tosjah_rzCPw        3.5
25    dusNIzdCaH6EoLl2hRy6cQ        3.5
26    CTN5Z3fs3jFHfyma8XxzVg        3.5
27    7v-2HkyrfYkPf471v4gCmg        2.0
28    hgQOESYp7CF4LnNI90XEiw        3.5
29    BNDP3up8Ltn7oVXEt4YLqw        3.5
30    F06m2yQSPHIrb1IT7heYeQ        4.0
31    gFjHMjQXn5pbObxJupiuPA        5.0
32    X3s0BN02lS6EigSnJaSyDw        3.5
33    q4i-GbjeSp6ucBDXGE9DqA        4.5
34    X2qnigcKuTWL7x9fS2ZUdw        4.0
35    H2Chxto2e6dHTDJ8-s3-pQ        3.0
36    DZkVWxknDUuWX0-wmtGhQw        3.0
37    SGPjYRy6x7R5ZlGa_nrskg        2.0
38    VVLGIq6ksrgGSfi7VBTmpg        4.0
39    yKpdzrqe_qIbu9dB6bj9Gg        2.5
40    lXCmTGagqHuPgaeN2g2P1Q        3.5
41    tk7__jHNlFMsfShjv5CJNQ        4.0
42    8bZ49zy4KlFVu5teFETYhQ        3.5
43    UIWt3IP92R5ELw3UQxZoeg        5.0
44    SAfuIUZMXrOnb3LWyvYjDA        3.5
45    vHIUZzeWg7VxL9Y-hrE43g        2.0
46    DMMEWBNOJhB9nG_2J1lYvg        3.0
47    aidcfUzZLOjWgwlxfv3UlA        3.0
48    7B5kcuCUkQD3AI3vqFI2cA        3.5
49    W3ia8dkoGGRYEfFg_BiyPg        2.5
50    e1DfwqDhYQYLKoyHmJu0hQ        4.5
51    3rFnH0MlGquQApfr4ss13Q        4.0
52    V78f9CdEVTkKFkyhdTYVrQ        3.5
53    ghc7Yqr7RkNbj3ydTpGuRQ        4.5
54    M5A5r0HbMRfTzidqMKYHfw        4.0
55    9phyjc0gaJTRO_YFJDH6mg        4.5
56    yYkvonvBGZB6UMnpzr6Ryw        2.5
57    iT_z6pzoK1AbqaBrDbXhlQ        4.0
58    -xX-Vjol_fwWaN2mn1F1wg        3.5
59    6Ege_N9uJ-rtKIs1TNA8aQ        2.5
60    vZLrA1A0rNebyMtxBwOCDQ        4.5
61    kds044HPuEB_HzoR_EHLeQ        3.5
62    I6qFvR-jVDGqDD_iVG38ng        3.0
63    2xbxXWeu3tpZEJdGTTGbLg        3.5
64    VR2LTEsJByan97fcYRkl5w        3.0
65    i0ToFQWsWPzFEC1eAxBh6Q        2.5
66    FMOWO7_mj8lSZnV3WqpGiA        3.5
67    UcBgxABVMc5mo1JLB8t70Q        3.0
68    7vWb1Afpm2arr8NCaE_EyQ        4.5
69    N4r3XX7uH42aXhHvFMkxjA        3.0
70    ohz8ljVxcZMo2bMGrBZfgw        3.5
71    vAbRNF0hJt91oCUpm_sdKw        3.5
72    QcdKTLeP3J5Ki-fVcPZkfA        4.0
73    Q-dVQgyof9paXKJLwFsn3Q        2.0
74    E9cD-weHeU6TMf-VPKfPMQ        1.5
75    F3jMS4aNQI6tPtjH61decw        4.0
76    BIbjBxoiJLS8CnNsSP64TQ        2.0
77    phLWnouPKgNkoRtS6wCYgQ        4.0
78    eVvnRqb4GSJUfN5k2-9oOQ        4.0
79    bZs7FJ7fHIJxVecfp1qvug        4.0
80    shSYKGuSzXpctURCR9kCFQ        3.0
81    v2UKNMDqWN1UaWlK2Ugx2Q        3.5
82    GMrwDXRlAZU2zj5nH6l4vQ        4.0
83    MXpCVzm1V5OH05KO6n7ntA        5.0
84    K4z0ODOZNuN2uRnL4IwApw        3.0
85    H2FohfCm8kVorCEzESF1MA        3.0
86    qVO3l9Q0-KVQE7W9JL9ePw        4.0
87    I8T4Xsp3Wv7W-RJhsHrTDA        3.5
88    LO5wXyFY6KUYleg0ZK5xiw        4.5
89    2qITBvSPsrXJPutDevpNOQ        2.5
90    iX2c4IzH_L5F6FM5GD3SUQ        4.5
91    ujHiaprwCQ5ewziu0Vi9rw        3.5
92    vn-vRefiIb92Y7pniF6ypA        3.5
93    G1lB2bUf1MT1FZT8TBy62g        4.5
94    vfqUUh_5KF3R7mz2XiNXGg        5.0
95    DVfCbJhJUDWRlUfrKzaKOA        2.0
96    Kbidfh24_7-a380tovQeYA        3.5
97    DUeqWfBI90UBR6xSYQO3uw        3.0
98    aBCqrJwXAHnTgO2e_l0v8w        2.0
99    CH4my_JJ7PJ

In [19]:
review_restaurant = pd.read_csv('yelp_dataset/review_restaurant.csv')
review_restaurant

/Users/hayley/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning: Columns (0,2) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Unnamed: 0             business_id cool                 date  funny  \
0                0  PZ-LZzSlhSe9utkQYU8pFg    0  2011-06-29 02:55:07    0.0   
1                1  PZ-LZzSlhSe9utkQYU8pFg    0  2010-10-06 18:20:13    0.0   
2                2  PZ-LZzSlhSe9utkQYU8pFg    0  2010-01-13 00:35:45    0.0   
3                3  PZ-LZzSlhSe9utkQYU8pFg    0  2008-08-23 20:30:33    0.0   
4                4  PZ-LZzSlhSe9utkQYU8pFg    0  2009-06-01 20:02:55    0.0   
5                5  PZ-LZzSlhSe9utkQYU8pFg    0  2010-05-22 16:54:57    0.0   
6                6  PZ-LZzSlhSe9utkQYU8pFg    0  2008-09-01 21:55:05    0.0   
7                7  PZ-LZzSlhSe9utkQYU8pFg    0  2015-04-03 03:59:34    0.0   
8                8  PZ-LZzSlhSe9utkQYU8pFg    0  2011-05-06 03:31:40    0.0   
9                9  PZ-LZzSlhSe9utkQYU8pFg    2  2010-08-29 16:19:05    0.0   
10              10  PZ-LZzSlhSe9utkQYU8pFg    0  2011-01-16 03:09:05    0.0   
11              11  PZ-LZzSlhSe9utkQYU8pFg    0  2011-03-29 00:39:22    1.0   
12              12  PZ-LZzSlhSe9utkQYU8pFg    1  2007-08-23 06:01:28    3.0   
13              13  PZ-LZzSlhSe9utkQYU8pFg    0  2010-07-20 10:09:55    0.0   
14              14  PZ-LZzSlhSe9utkQYU8pFg    1  2016-08-09 19:02:44    0.0   
15              15  PZ-LZzSlhSe9utkQYU8pFg    1  2010-03-28 00:36:36    0.0   
16              16  PZ-LZzSlhSe9utkQYU8pFg    0  2011-03-30 20:36:07    0.0   
17              17  PZ-LZzSlhSe9utkQYU8pFg    0  2009-08-30 07:26:47    0.0   
18              18  PZ-LZzSlhSe9utkQYU8pFg    1  2010-01-27 04:17:13    0.0   
19              19  PZ-LZzSlhSe9utkQYU8pFg    1  2011-02-27 16:01:22    1.0   
20              20  PZ-LZzSlhSe9utkQYU8pFg    0  2010-12-17 20:30:54    0.0   
21              21  PZ-LZzSlhSe9utkQYU8pFg    1  2011-06-08 19:55:43    0.0   
22              22  PZ-LZzSlhSe9utkQYU8pFg    1  2011-04-01 06:18:12    2.0   
23              23  PZ-LZzSlhSe9utkQYU8pFg    0  2009-09-06 05:11:50    2.0   
24              24  PZ-LZzSlhSe9utkQYU8pFg    1  2011-07-17 18:39:52    0.0   
25              25  PZ-LZzSlhSe9utkQYU8pFg    0  2010-04-05 22:45:35    1.0   
26              26  PZ-LZzSlhSe9utkQYU8pFg    0  2011-06-27 15:51:04    0.0   
27              27  PZ-LZzSlhSe9utkQYU8pFg    0  2011-03-01 18:39:17    0.0   
28              28  PZ-LZzSlhSe9utkQYU8pFg    0  2010-04-27 00:40:09    0.0   
29              29  PZ-LZzSlhSe9utkQYU8pFg    1  2007-11-01 00:18:12    0.0   
30              30  PZ-LZzSlhSe9utkQYU8pFg    0  2014-03-31 05:57:20    0.0   
31              31  PZ-LZzSlhSe9utkQYU8pFg    0  2009-07-23 15:45:59    0.0   
32              32  PZ-LZzSlhSe9utkQYU8pFg    0  2010-02-17 23:43:54    0.0   
33              33  PZ-LZzSlhSe9utkQYU8pFg    0  2009-04-16 18:05:36    0.0   
34              34  PZ-LZzSlhSe9utkQYU8pFg    0  2011-12-13 20:28:35    0.0   
35              35  PZ-LZzSlhSe9utkQYU8pFg    0  2011-01-28 00:53:08    0.0   
36              36  PZ-LZzSlhSe9utkQYU8pFg    2  2009-07-02 16:43:17    2.0   
37              37  PZ-LZzSlhSe9utkQYU8pFg    0  2010-11-18 02:34:38    0.0   
38              38  PZ-LZzSlhSe9utkQYU8pFg    0  2010-05-12 05:54:48    1.0   
39              39  PZ-LZzSlhSe9utkQYU8pFg    0  2007-11-09 16:13:07    1.0   
40              40  PZ-LZzSlhSe9utkQYU8pFg    1  2010-11-21 05:13:50    1.0   
41              41  KWywu2tTEPWmR9JnBc0WyQ    1  2017-02-19 09:17:53    0.0   
42              42  KWywu2tTEPWmR9JnBc0WyQ    0  2014-05-26 21:42:00    0.0   
43              43  KWywu2tTEPWmR9JnBc0WyQ    1  2014-03-14 20:58:58    0.0   
44              44  KWywu2tTEPWmR9JnBc0WyQ    0  2015-11-20 05:24:45    1.0   
45              45  KWywu2tTEPWmR9JnBc0WyQ    0  2018-03-16 07:47:23    0.0   
46              46  KWywu2tTEPWmR9JnBc0WyQ    1  2015-10-24 05:25:31    0.0   
47              47  KWywu2tTEPWmR9JnBc0WyQ    0  2014-11-13 21:21:04    0.0   
48              48  KWywu2tTEPWmR9JnBc0WyQ    2  2015-10-24 09:05:39    1.0   
49              49  KWywu2tTEPWmR9JnBc0WyQ    0  2017-02-2

In [31]:
restaurant_review_stars = pd.merge(review_restaurant, df_edit_restaurant, on='business_id' ,how='left')
restaurant_review_stars.to_csv('./yelp_dataset/restaurant_review_stars.csv')

In [187]:
user_review_cnt = review_restaurant.groupby("user_id").agg({"count"})["stars"].sort_values("count") 
user_review_cnt
user_review_cnt.to_csv('./yelp_dataset/user_review_cnt.csv')

In [184]:
grp = restaurant_review_stars.groupby("business_id").agg({"mean","count"})["stars"]
grp

mean  count
business_id                            
--9e1ONYQuAa-CB_Rrw7Tw  4.125828   1661
--q7kSBRb0vWC8lSkXFByA  4.000000      7
-0BxAGlIk5DJAGVkpqBXxg  2.977273     44
-0RkJ_uIduNLWQrphbADRw  4.301587     63
-0VImVWDeqewaA3th8fzIg  5.000000     27
-153AjTW5luZPK4omEujWA  3.000000      5
-1m9o3vGRA8IBPNvNqKLmA  4.559846    259
-1uVyyy3UXNA9WoPucNniA  4.589744     39
-1vfRrlnNnNJ5boOVghMPA  3.289157     83
-3H_6UZGWrfl8XQsm1fBmw  2.428571      7
-3zffZUHoY8bQjGfPSoBKQ  4.044410    653
-46pFijv3f2jZH-_Ze6CQA  3.913043     23
-8R_-EkGpUhBk55K9Dd4mg  3.655738    122
-8ZiMXZReeTD3kwEvS0Lww  4.412214    131
-95mbLJsa0CxXhpaNL4LvA  3.690217    736
-9Ir5OiFiOszIgeFgalXcw  3.023256     43
-9YyInW1wapzdNZrhQJ9dg  2.489691    194
-AD5PiuJHgdUcAK-Vxao2A  3.590323    310
-ADtl9bLp8wNqYX1k3KuxA  4.111336    494
-AGdGGCeTS-njB_8GkUmjQ  4.250000      8
-AUh0iDyhLV6OfXloHPl0Q  2.272727     11
-B1PzLYsOSL9rda--Wr7tQ  4.200000      5
-BAOJ8aA5MCrYx_tQUyZHg  4.416667     24
-BS4aZAQm9u41YnB9MUASA  4.653846     78
-Bf8BQ3yMk8U2f45r2DRKw  3.845361    194
-BmqghX1sv7sgsxOIS2yAg  3.984375    192
-Bv-HHUs8aHzDrdWcZHn8w  3.157303     89
-C8sSrFqaCxp51pyo-fQLQ  4.536765    136
-CQokjildrY7UZezXCdEBw  4.809524     42
-CZwX0Fy14DGCY_2aFkhKg  3.333333      6
-CbDQXiuKzPQ0_jiUz03aw  3.941176     51
-EohS3nXZGl6odE9Lx5BSw  1.666667     12
-ErwgUmZ1-jHW_rSu55jlg  4.000000     36
-FNquqGseSCVMWo7KbK-Tg  3.510791    139
-FcZY7a7qgxTUlTvwuyJnQ  3.462963    270
-FlrlELIGmCqdt_JxbdFgg  2.888889      9
-G7MPSNBpxRJmtrJxdwt7A  3.222222     54
-G9DFmuokdYk_H35ezRkAw  4.125000      8
-INdswGdyRyy72xXHalNbg  3.062893    159
-IWsoxH7mLJTTpU5MmWY4w  3.842907    853
-JFVxwdVQfX207554dx1nw  3.425676    148
-JfncbVURtvuzBbof40o1w  2.535211    142
-Jo0rJr2mZxBVgaJqDs-TQ  3.333333      6
-Jx2rd2rH7MlWfb9RMtCFQ  3.628571     35
-K82LBrI3H0FVuhTbNDpRA  3.361940    268
-KUOQZxJqGjf4NfK3j43tQ  2.687500     16
-LG_SXZrWLTnfSXRPZQvzA  1.000000      4
-LMycE26AortJDsbc8oXOg  2.800000     40
-Le6cwbZL4tDZwNHwipfKg  4.283186    452
-LmxQLtHixUTeQkk5G-gTw  4.718750     32
-LyGT6bztmvWd3_pa93YDg  3.166667      6
-LzUYsR54hd8cCiYXTquRA  3.161926    457
-MmAW2x9vMGuhVcALU7QRw  1.833333      6
-NR4KqS6lHseNvJ-GFzfMA  4.274074    135
-N_agk8RUHvHk3GVDsyunQ  4.179487     78
-NjZ5HZApXjRJaTVZeSO_w  3.837838     37
-NsIO9AUNEmbsxdUORtfAQ  4.857143      7
-OEIW0dO96-492qa_luxaw  3.989655    290
-P8dGzSVhJi-5oZ-8U2y0w  2.436620     71
-PGsEXB6DFTVKa1eDOlzWA  3.444015    259
-PRTv5z2N687DEyW0Fkcww  2.923077     13
-Pv-3Moxm6is6COkQIA7Kg  4.700000     10
-QNQ4R1VgRoL4b6lC8Anrg  2.984733    131
-Qamd1hK7jczDkdUrm8lxg  4.800000      5
-Qkx7W0itbAApcG5lJuMFQ  4.301546    388
-RJ216TTIghZshCkUlD1WQ  4.460815    319
-R_u_4Ya8ceUN7qDlvIQTg  5.000000      3
-RdenSl5COgnPqaANI3kCQ  3.500000     28
-SGZcGqnsp_uRIjKP2RGZg  3.363636     11
-SWWUof5TuWDVL5SEAml8Q  3.600000      5
-SpT8Tyz2R45zSw1AIUimQ  2.965986    147
-Tv5UZeFHdKz3RM9vOYpaw  2.600000      5
-U7tvCtaraTQ9b0zBhpBMA  2.647458   1180
-Uix-n4Jqo4W7ERagC5qAA  3.793103     87
-UtYWvCnUppcSaC_u1pTYQ  4.000000      5
-VV6BJwqymr2-VPp_jFCPg  2.764706     17
-WLrZPzjKfrftLWaCi1QZQ  4.021940    866
-WQhVJnBmyapFn0digQJwg  4.421053     19
-WfV03-dVE3HSMUmg0tnvQ  3.517241     58
-XKG6GamlSBwy5AcXQGAfA  3.000000      7
-YCd2_DdJUeZx3RRcmIZ_g  2.413793     29
-YWr1wm_NaAlgEf9TZzsMQ  2.201923    104
-Ylpy3VyRWwubf9dysuwjQ  3.729690    677
-_TSaVr53qiEGqMkwyEMaQ  4.195519    491
-_yEVC3_3M6YOsamYfNFEw  3.830097    206
-a43zqioXNOjx_QejRS9FA  4.222222      9
-a857YYdjzgOdOjFFRsRXQ  3.633880    549
-blcoBWe_z8B2I9XVESvjQ  3.666667      3
-byybpV9bP2k0aJ6-WhiBA  4.483871     62
-cOVyWUJlasj-wpMAaWwvQ  4.375000     48
-cxD1NimFldATDUsN-oa3A  2.217391     23
-dGORHtjPRnQzTZ2-SYa_g  3.062500     32
-ed0Yc9on37RoIoG2ZgxBA  4.097993   1694
-fJ8qqZN4wg2o2VoRlYfAw  5.000000      5
-gXDD2oSHBDA3zgjX6g9pQ  4.100000     30
-g_3XHnCdchIchtC-le2tQ  4.304348     23
-heiUEHVRPHo5xaAE8vwTg  4.666667     27
-hzQQ8tbXThpp0k5E_y1Dw  2.949367     79
-iBk1_3M_efQtY6Bcygp5w  4.44

In [39]:
tmp = pd.merge(grp, df_edit_restaurant, on='business_id' ,how='left').sort_values("count")



business_id      mean  count  biz_stars
290                        1       NaN      0        NaN
1120  7B5kcuCUkQD3AI3vqFI2cA  3.666667      3        3.5
8449  wvyRHhvnOaJFf2CSVQVgVQ  4.000000      3        4.0
5172  Zsb1fveuV7sIYJogNsbzIA  5.000000      3        5.0
1313  8_NAyTr8z80SOrHY2wImQA  4.000000      3        4.0
1525  9xZ2AURznQzx1MwEWBFNQA  3.666667      3        3.5
8460  x2XWGOmomfKyfHmSy17yRA  2.333333      3        2.5
8464  x4Qw9PZGDhK6-bJsskD0Ww  4.000000      3        4.0
5939  edk5jsx7L3dzMWPcoCE3Wg  2.666667      3        2.5
783   4n81G-pmC3rfhmaPsbwYKg  4.666667      3        4.5
4546  V_bdNk4zSuXRRG07I0aF7Q  3.000000      3        3.0
3766  QGDwLtD4mUUHBqvQe1QZFQ  3.666667      3        3.5
5337  aDSSDo6IFnogUnBQKL5-lw  3.333333      3        3.5
2399  G5SKZd8F52XsKe8tdTwHQQ  4.666667      3        4.5
2193  EgyGpJ50LNS6uXk6fkZM4Q  3.333333      3        3.5
4797  XKVWYoKaIR1CEoxMYMFPXw  3.000000      3        3.0
1306  8VzVFHFgI_RzZAKzq_aK9g  1.666667      3        1.5
1304  8V2Luk8CNjdE5oP2kQLNag  4.666667      3        4.5
3417  NieVNg1pP-PPeGUsdpy9BA  4.000000      3        4.0
5168  Zrtozs1rdJREGNxFRTcV3Q  2.333333      3        2.5
6552  j9UX-w0YQKXY6YuERT6BHA  2.333333      3        2.5
6553  j9qC2kxTFcgApOjQ0kvuVQ  3.333333      3        3.5
1300  8StUtYZ3yTCDxMS9439GMQ  4.333333      3        4.5
7454  pkLTIRavTCtjCdhQgl6T2w  2.000000      3        2.0
5167  ZriDpPXjStMI-uBUkovVUQ  4.666667      3        4.5
344   1PLDegYBS2GgyVhX7RoMyA  2.333333      3        2.5
3422  Nk8rRsl9u4GrbxEeEVsedg  2.666667      3        2.5
8019  u12EUBQJoPDtyPQyKa7zTw  1.666667      3        1.5
7210  nmWLUc5MmX3FLLVmK4fVHQ  3.666667      3        3.5
8478  xDHYlBjfwMVIWDUGFjOPxA  4.000000      3        4.0
5938  ec1xAYXFKc5P7as_uIbzUA  1.333333      3        1.5
7232  nvEMLcfkhx_Eo6wDvFsLPQ  3.666667      3        3.5
5800  dd3lBUGkokm3P1ChWJnYuw  3.333333      3        3.5
1507  9r6ijZgxDLJFysxIohtTcQ  2.333333      3        2.5
1509  9rl5QAI-uE5M38bqM6uX6w  4.333333      3        4.5
6828  lCaDQzQcBB4G-5J5j5SOjQ  4.000000      3        4.0
8081  uTZKDwO13D-V26kSct5guQ  1.000000      3        1.0
741   4SPd65eJ1K0KiBPvXpo50A  3.000000      3        3.0
742   4Tie5rrC4mQA32yik0s3pw  5.000000      3        5.0
5924  eWYpJIv1xDaNAmRTT_WjeQ  3.000000      3        3.0
413   1tCy2a6unETa6yJFK3491Q  2.333333      3        2.5
4766  X4iL3xDp_go6xHj126K3fw  2.333333      3        2.5
4571  Vk-TBQwwvC5ehW6iF1_psg  5.000000      3        5.0
5534  bcpCJ7q9_HXO53eaeuIZrw  4.333333      3        4.5
8426  wmFd0FzFCCXvSegbAdJLRg  3.333333      3        3.5
6375  hs1SejlpCnNzVwpY2enGCg  3.666667      3        3.5
3751  Q8r_5tb0hoMQZ8IkNy_lPg  3.666667      3        3.5
6927  ltELYeBXsbkQPlH16e-mOg  2.000000      3        2.0
2721  IUPkcr2VORvper0Q8aJkTg  5.000000      3        5.0
6364  hmRR9whRtnbV5LyIC3Bxrg  3.666667      3        3.5
749   4WS9os_Dj5nckxeNsva6Vg  3.666667      3        3.5
399   1lByA5pD2YVqqH4_8tOBzw  3.333333      3        3.5
5323  a5IOLO2APwxDAyNepO-WWQ  2.333333      3        2.5
2835  JNCPSRNSGpfSIpaOuQ6hyg  4.333333      3        4.5
8433  wpHN9iLlhn_z613xJd5uyA  2.000000      3        2.0
4564  Vh48UKeGt31a8g5TYHRIqw  4.333333      3        4.5
8060  uGlxpR3HAyqBsOf1HTvkvQ  3.333333      3        3.5
8054  uEMrBEw8En3yEzquXqeEuw  4.333333      3        4.5
8441  wraKox0MBW_w449VJXVenQ  3.666667      3        3.5
2993  KbdX47BHUL1XtG74TMlBXg  5.000000      3        5.0
3780  QP2c6C_xk6nSiLgaVuq2hQ  1.666667      3        1.5
2833  JMpATuCfHzeP-DASD7DpXQ  4.000000      3        4.0
8013  tymwLL-lf2ic92293k6LHQ  3.000000      3        3.0
4802  XOghoJuzkuHDS-8IZBPTHw  5.000000      3        5.0
6306  hL1r-Mh-UPOQJ7tbXCd9Yw  3.000000      3        3.0
4494  VEb4csHZ3dirJstcA8eLAw  1.000000      3        1.0
2162  EV85dKbe4lYRC3Mo4rNXVQ  4.333333      3        4.5
4842  Xh-XorzPitxXtOwXmAvgfw  4.333333      3        4.5
8540  xg6X-QhO5kTv9PtFqJp-OA  4.333333      3        4.5
3710  Pp6jOkxejp0WheNCajZIi

In [120]:
# 0-100, 101- 500, 501 - 1000, 1001 - 2000, 2001-3000, 3000-4000, 4000-5000, 5000 
def test_func(df):
    if (df["count"] >= 1 and df["count"] <= 100):
        val = 0.1
    elif df["count"] > 101 and df["count"] <= 500:
        val =0.2
    elif df["count"] > 501 and df["count"] <= 1000:
        val = 0.3
    elif df["count"] > 1001 and df["count"] <= 2000:
        val = 0.4
    elif df["count"] > 2001 and df["count"] <= 3000:
        val = 0.5
    elif df["count"] > 3001 and df["count"] <= 4000:
        val= 0.6
    elif df["count"] > 4001 and df["count"] <= 5000:
        val= 0.7
    else:
        val= 0.8
    return val

In [121]:
#df['C'] = df.apply(f, axis=1)

tmp["weight"] = tmp.apply(test_func, axis=1)

In [132]:
tmp1 = tmp[["business_id","weight"]]
tmp1

business_id  weight
290                        1     0.8
1120  7B5kcuCUkQD3AI3vqFI2cA     0.1
8449  wvyRHhvnOaJFf2CSVQVgVQ     0.1
5172  Zsb1fveuV7sIYJogNsbzIA     0.1
1313  8_NAyTr8z80SOrHY2wImQA     0.1
1525  9xZ2AURznQzx1MwEWBFNQA     0.1
8460  x2XWGOmomfKyfHmSy17yRA     0.1
8464  x4Qw9PZGDhK6-bJsskD0Ww     0.1
5939  edk5jsx7L3dzMWPcoCE3Wg     0.1
783   4n81G-pmC3rfhmaPsbwYKg     0.1
4546  V_bdNk4zSuXRRG07I0aF7Q     0.1
3766  QGDwLtD4mUUHBqvQe1QZFQ     0.1
5337  aDSSDo6IFnogUnBQKL5-lw     0.1
2399  G5SKZd8F52XsKe8tdTwHQQ     0.1
2193  EgyGpJ50LNS6uXk6fkZM4Q     0.1
4797  XKVWYoKaIR1CEoxMYMFPXw     0.1
1306  8VzVFHFgI_RzZAKzq_aK9g     0.1
1304  8V2Luk8CNjdE5oP2kQLNag     0.1
3417  NieVNg1pP-PPeGUsdpy9BA     0.1
5168  Zrtozs1rdJREGNxFRTcV3Q     0.1
6552  j9UX-w0YQKXY6YuERT6BHA     0.1
6553  j9qC2kxTFcgApOjQ0kvuVQ     0.1
1300  8StUtYZ3yTCDxMS9439GMQ     0.1
7454  pkLTIRavTCtjCdhQgl6T2w     0.1
5167  ZriDpPXjStMI-uBUkovVUQ     0.1
344   1PLDegYBS2GgyVhX7RoMyA     0.1
3422  Nk8rRsl9u4GrbxEeEVsedg     0.1
8019  u12EUBQJoPDtyPQyKa7zTw     0.1
7210  nmWLUc5MmX3FLLVmK4fVHQ     0.1
8478  xDHYlBjfwMVIWDUGFjOPxA     0.1
5938  ec1xAYXFKc5P7as_uIbzUA     0.1
7232  nvEMLcfkhx_Eo6wDvFsLPQ     0.1
5800  dd3lBUGkokm3P1ChWJnYuw     0.1
1507  9r6ijZgxDLJFysxIohtTcQ     0.1
1509  9rl5QAI-uE5M38bqM6uX6w     0.1
6828  lCaDQzQcBB4G-5J5j5SOjQ     0.1
8081  uTZKDwO13D-V26kSct5guQ     0.1
741   4SPd65eJ1K0KiBPvXpo50A     0.1
742   4Tie5rrC4mQA32yik0s3pw     0.1
5924  eWYpJIv1xDaNAmRTT_WjeQ     0.1
413   1tCy2a6unETa6yJFK3491Q     0.1
4766  X4iL3xDp_go6xHj126K3fw     0.1
4571  Vk-TBQwwvC5ehW6iF1_psg     0.1
5534  bcpCJ7q9_HXO53eaeuIZrw     0.1
8426  wmFd0FzFCCXvSegbAdJLRg     0.1
6375  hs1SejlpCnNzVwpY2enGCg     0.1
3751  Q8r_5tb0hoMQZ8IkNy_lPg     0.1
6927  ltELYeBXsbkQPlH16e-mOg     0.1
2721  IUPkcr2VORvper0Q8aJkTg     0.1
6364  hmRR9whRtnbV5LyIC3Bxrg     0.1
749   4WS9os_Dj5nckxeNsva6Vg     0.1
399   1lByA5pD2YVqqH4_8tOBzw     0.1
5323  a5IOLO2APwxDAyNepO-WWQ     0.1
2835  JNCPSRNSGpfSIpaOuQ6hyg     0.1
8433  wpHN9iLlhn_z613xJd5uyA     0.1
4564  Vh48UKeGt31a8g5TYHRIqw     0.1
8060  uGlxpR3HAyqBsOf1HTvkvQ     0.1
8054  uEMrBEw8En3yEzquXqeEuw     0.1
8441  wraKox0MBW_w449VJXVenQ     0.1
2993  KbdX47BHUL1XtG74TMlBXg     0.1
3780  QP2c6C_xk6nSiLgaVuq2hQ     0.1
2833  JMpATuCfHzeP-DASD7DpXQ     0.1
8013  tymwLL-lf2ic92293k6LHQ     0.1
4802  XOghoJuzkuHDS-8IZBPTHw     0.1
6306  hL1r-Mh-UPOQJ7tbXCd9Yw     0.1
4494  VEb4csHZ3dirJstcA8eLAw     0.1
2162  EV85dKbe4lYRC3Mo4rNXVQ     0.1
4842  Xh-XorzPitxXtOwXmAvgfw     0.1
8540  xg6X-QhO5kTv9PtFqJp-OA     0.1
3710  Pp6jOkxejp0WheNCajZIig     0.1
4081  SOX-F4C7WcpWohSL47uEJw     0.1
3439  Nu0GjN3HeFomQ5ArsJacKQ     0.1
5147  Ziqzfvpp2cpZAu0OwjiD5w     0.1
278   0xNSLnqLT5miZO9RqSvbhw     0.1
866   5MjT_Dxc0VKVbd2NNPNc_A     0.1
3703  PmXkNyXb2r7Y43gMeQiafQ     0.1
4089  SSWrPxJQ7ezB17OGwLUkWQ     0.1
5637  cQjM4o-4SOSmLemQSx6WsQ     0.1
8562  xo4JdGUuHQapOnQ4VIfN0Q     0.1
2673  I9b_caW4NBZ5H_eGkaVxow     0.1
6966  m8u3fsbhfdXu7IhXeHBO5A     0.1
4091  ST-IVOkIRq-DAyTD0e9DKw     0.1
2446  GRLHdCXzmFCBbvvjRxXnrA     0.1
7163  nQ7L1yfQs-ZY4_U1reSMwQ     0.1
265   0rTKqrcikxRKbJcukNjrLA     0.1
5141  ZgrKt3GU8vYyeE7pqSUkkQ     0.1
1587  AQ-H-lvkoB8DOFYdRmkceA     0.1
873   5OLtY1-xR6LjeH3kJGJ5UA     0.1
5639  cRTMAbJiyd6xJ9eKj357YQ     0.1
7151  nL2dCPpH5LUYYkDkNVdliQ     0.1
8572  xrt83taykZS48LB21yOB9w     0.1
8583  xxP4s5X2PlOW6OkFoeBX2A     0.1
3084  LAoK-5hDjqALXQ9F6RrVIw     0.1
6799  kyQQPAqO_Ns5kFZI4Gqg1g     0.1
293   11y02mqvQyJf0R8LImw3xA     0.1
1881  CcMi0EM4KFqa_4hVe1oN3g     0.1
7202  nhzYBNrFYvqMzOeudevxNQ     0.1
8504  xQa1-m8CwbhGpCUt5SBXog     0.1
3236  MJzXwfIuZF6bkStK8wjBog     0.1
2178  Eau1XrNg91XSzJRn_sCWTg     0.1
...                      ...     ...
2751  IhNASEZ3XnBHmuuVnWdIwA     0.4
2700  IMLrj2klosTFvPRLv56cng     0.4
6250  gx2yPrOJSwF1ApJYdGBWIw     0.4
7397  pHJu8tj3sI8eC5aIHLFEfQ     0.4
6040  fQt4D34vcJNtEf8Q4zte3w     0.4
5619  cJWbbvGmyhFiBpG_5hf5LA     0.4
1530  A-uZAD4zP3rRxb4

In [133]:
tmp2 = pd.merge(restaurant_review_stars, tmp1, on='business_id' ,how='left')
tmp2

Unnamed: 0             business_id cool                 date  funny  \
0                0  PZ-LZzSlhSe9utkQYU8pFg    0  2011-06-29 02:55:07    0.0   
1                1  PZ-LZzSlhSe9utkQYU8pFg    0  2010-10-06 18:20:13    0.0   
2                2  PZ-LZzSlhSe9utkQYU8pFg    0  2010-01-13 00:35:45    0.0   
3                3  PZ-LZzSlhSe9utkQYU8pFg    0  2008-08-23 20:30:33    0.0   
4                4  PZ-LZzSlhSe9utkQYU8pFg    0  2009-06-01 20:02:55    0.0   
5                5  PZ-LZzSlhSe9utkQYU8pFg    0  2010-05-22 16:54:57    0.0   
6                6  PZ-LZzSlhSe9utkQYU8pFg    0  2008-09-01 21:55:05    0.0   
7                7  PZ-LZzSlhSe9utkQYU8pFg    0  2015-04-03 03:59:34    0.0   
8                8  PZ-LZzSlhSe9utkQYU8pFg    0  2011-05-06 03:31:40    0.0   
9                9  PZ-LZzSlhSe9utkQYU8pFg    2  2010-08-29 16:19:05    0.0   
10              10  PZ-LZzSlhSe9utkQYU8pFg    0  2011-01-16 03:09:05    0.0   
11              11  PZ-LZzSlhSe9utkQYU8pFg    0  2011-03-29 00:39:22    1.0   
12              12  PZ-LZzSlhSe9utkQYU8pFg    1  2007-08-23 06:01:28    3.0   
13              13  PZ-LZzSlhSe9utkQYU8pFg    0  2010-07-20 10:09:55    0.0   
14              14  PZ-LZzSlhSe9utkQYU8pFg    1  2016-08-09 19:02:44    0.0   
15              15  PZ-LZzSlhSe9utkQYU8pFg    1  2010-03-28 00:36:36    0.0   
16              16  PZ-LZzSlhSe9utkQYU8pFg    0  2011-03-30 20:36:07    0.0   
17              17  PZ-LZzSlhSe9utkQYU8pFg    0  2009-08-30 07:26:47    0.0   
18              18  PZ-LZzSlhSe9utkQYU8pFg    1  2010-01-27 04:17:13    0.0   
19              19  PZ-LZzSlhSe9utkQYU8pFg    1  2011-02-27 16:01:22    1.0   
20              20  PZ-LZzSlhSe9utkQYU8pFg    0  2010-12-17 20:30:54    0.0   
21              21  PZ-LZzSlhSe9utkQYU8pFg    1  2011-06-08 19:55:43    0.0   
22              22  PZ-LZzSlhSe9utkQYU8pFg    1  2011-04-01 06:18:12    2.0   
23              23  PZ-LZzSlhSe9utkQYU8pFg    0  2009-09-06 05:11:50    2.0   
24              24  PZ-LZzSlhSe9utkQYU8pFg    1  2011-07-17 18:39:52    0.0   
25              25  PZ-LZzSlhSe9utkQYU8pFg    0  2010-04-05 22:45:35    1.0   
26              26  PZ-LZzSlhSe9utkQYU8pFg    0  2011-06-27 15:51:04    0.0   
27              27  PZ-LZzSlhSe9utkQYU8pFg    0  2011-03-01 18:39:17    0.0   
28              28  PZ-LZzSlhSe9utkQYU8pFg    0  2010-04-27 00:40:09    0.0   
29              29  PZ-LZzSlhSe9utkQYU8pFg    1  2007-11-01 00:18:12    0.0   
30              30  PZ-LZzSlhSe9utkQYU8pFg    0  2014-03-31 05:57:20    0.0   
31              31  PZ-LZzSlhSe9utkQYU8pFg    0  2009-07-23 15:45:59    0.0   
32              32  PZ-LZzSlhSe9utkQYU8pFg    0  2010-02-17 23:43:54    0.0   
33              33  PZ-LZzSlhSe9utkQYU8pFg    0  2009-04-16 18:05:36    0.0   
34              34  PZ-LZzSlhSe9utkQYU8pFg    0  2011-12-13 20:28:35    0.0   
35              35  PZ-LZzSlhSe9utkQYU8pFg    0  2011-01-28 00:53:08    0.0   
36              36  PZ-LZzSlhSe9utkQYU8pFg    2  2009-07-02 16:43:17    2.0   
37              37  PZ-LZzSlhSe9utkQYU8pFg    0  2010-11-18 02:34:38    0.0   
38              38  PZ-LZzSlhSe9utkQYU8pFg    0  2010-05-12 05:54:48    1.0   
39              39  PZ-LZzSlhSe9utkQYU8pFg    0  2007-11-09 16:13:07    1.0   
40              40  PZ-LZzSlhSe9utkQYU8pFg    1  2010-11-21 05:13:50    1.0   
41              41  KWywu2tTEPWmR9JnBc0WyQ    1  2017-02-19 09:17:53    0.0   
42              42  KWywu2tTEPWmR9JnBc0WyQ    0  2014-05-26 21:42:00    0.0   
43              43  KWywu2tTEPWmR9JnBc0WyQ    1  2014-03-14 20:58:58    0.0   
44              44  KWywu2tTEPWmR9JnBc0WyQ    0  2015-11-20 05:24:45    1.0   
45              45  KWywu2tTEPWmR9JnBc0WyQ    0  2018-03-16 07:47:23    0.0   
46              46  KWywu2tTEPWmR9JnBc0WyQ    1  2015-10-24 05:25:31    0.0   
47              47  KWywu2tTEPWmR9JnBc0WyQ    0  2014-11-13 21:21:04    0.0   
48              48  KWywu2tTEPWmR9JnBc0WyQ    2  2015-10-24 09:05:39    1.0   
49              49  KWywu2tTEPWmR9JnBc0WyQ    0  2017-02-2

In [116]:
tmp.groupby("weight").agg("count")["mean"]

weight
1    6127
2    2073
3     410
4     169
5      35
6      16
7       9
8      30
Name: mean, dtype: int64

In [137]:
tmp2["newStars"] = abs(tmp2.xs - tmp2.stars) * tmp2.weight + tmp2.stars

In [139]:
tmp2.to_csv('./yelp_dataset/edit_review.csv')

In [140]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import csv
from surprise import SVD,SVDpp,NMF,SlopeOne,NormalPredictor,KNNBaseline,KNNBasic,KNNWithMeans,KNNWithZScore,BaselineOnly,CoClustering
from surprise import Dataset
from surprise import Reader
from surprise import accuracy
from surprise.model_selection import train_test_split
from surprise.model_selection import GridSearchCV
from surprise.model_selection import cross_validate

In [144]:
df = tmp2[["user_id","business_id","newStars"]]

In [145]:
df

user_id             business_id  newStars
0        -Yz2wIcsdJxUOFMbTgoKQA  PZ-LZzSlhSe9utkQYU8pFg       5.1
1        jYcf_e5p0UG0S-9gJq_tNA  PZ-LZzSlhSe9utkQYU8pFg       4.0
2        nQC0JiPIk_jCooRDxpuw5A  PZ-LZzSlhSe9utkQYU8pFg       5.1
3        Gv_-mtOKhWFtCjn9xFe0SQ  PZ-LZzSlhSe9utkQYU8pFg       3.1
4        pabMYegF28KjHQ5hybAJ0A  PZ-LZzSlhSe9utkQYU8pFg       3.1
5        F_N4NyoMJWzBYFspeYfH3A  PZ-LZzSlhSe9utkQYU8pFg       4.0
6        oGYEaOv0IEUZ6kU3JFe98A  PZ-LZzSlhSe9utkQYU8pFg       4.0
7        EeKyqz_A6xeQ7ezuloqxyg  PZ-LZzSlhSe9utkQYU8pFg       5.1
8        ks6vHMFVaPACB18GO7XUig  PZ-LZzSlhSe9utkQYU8pFg       4.0
9        pngNlr9t4HObDgecGH_jaw  PZ-LZzSlhSe9utkQYU8pFg       4.0
10       SEYmHinZRVXiOFfqWCkuFA  PZ-LZzSlhSe9utkQYU8pFg       5.1
11       YMgZqBUAddmFErxLtCfK_w  PZ-LZzSlhSe9utkQYU8pFg       3.1
12       aKDe5qvoYT_1jdMOalehmQ  PZ-LZzSlhSe9utkQYU8pFg       2.2
13       rhH1Cqta8lb3n-t0fTRm5w  PZ-LZzSlhSe9utkQYU8pFg       4.0
14       BDjiEmXljD2ZHT61Iv9rrQ  PZ-LZzSlhSe9utkQYU8pFg       5.1
15       PFqhDyFta-8imsKa4bK3pQ  PZ-LZzSlhSe9utkQYU8pFg       5.1
16       98VVHG8CpPDf2zbSHqaB7w  PZ-LZzSlhSe9utkQYU8pFg       5.1
17       sDFQazfIy2uWvjrIjtlfLw  PZ-LZzSlhSe9utkQYU8pFg       4.0
18       2i_NkXLyuI_QtDa8FIaI3g  PZ-LZzSlhSe9utkQYU8pFg       5.1
19       KFWOn7x19RmrO6kzTJYmrQ  PZ-LZzSlhSe9utkQYU8pFg       5.1
20       F_N4NyoMJWzBYFspeYfH3A  PZ-LZzSlhSe9utkQYU8pFg       4.0
21       NEN5RFpZp7DE6K1PK2KZzg  PZ-LZzSlhSe9utkQYU8pFg       5.1
22       uUkYprg5GP-ExpexAP2s_g  PZ-LZzSlhSe9utkQYU8pFg       5.1
23       yi_4YTVS6XL7s5atKPbmpA  PZ-LZzSlhSe9utkQYU8pFg       1.3
24       imINxn9Q__xZ7VUk3JzX0Q  PZ-LZzSlhSe9utkQYU8pFg       5.1
25       mPU5Ar0NBOw_d95tIfTM0w  PZ-LZzSlhSe9utkQYU8pFg       2.2
26       L15JCA18Ib_vMUVJILxiSw  PZ-LZzSlhSe9utkQYU8pFg       4.0
27       NCNR0M5evdswD5y39-jVNw  PZ-LZzSlhSe9utkQYU8pFg       5.1
28       fOKiJUKlx95N2RSPPtyr5A  PZ-LZzSlhSe9utkQYU8pFg       4.0
29       9RkL3lRhtAkPUIVyB8_07Q  PZ-LZzSlhSe9utkQYU8pFg       4.0
30       owbC7FP8SNAlwv6f9S5Stw  PZ-LZzSlhSe9utkQYU8pFg       5.1
31       jo8vV5iUZLHp617cTKZ7mA  PZ-LZzSlhSe9utkQYU8pFg       5.1
32       5mkRo6VhwdYQ0X2qbBFE_Q  PZ-LZzSlhSe9utkQYU8pFg       5.1
33       HRyFtrmf19GTKEM_kOa2pg  PZ-LZzSlhSe9utkQYU8pFg       5.1
34       ZVn9FCVshH5yxfEKZKR5AQ  PZ-LZzSlhSe9utkQYU8pFg       5.1
35       Sv1C8Uly4dO1qtytcGMbyg  PZ-LZzSlhSe9utkQYU8pFg       1.3
36       AoII0-uM9z0EesGnb9YCjQ  PZ-LZzSlhSe9utkQYU8pFg       5.1
37       t7LwGCCew0LYbkpjoT_OZw  PZ-LZzSlhSe9utkQYU8pFg       4.0
38       15TfRqjx-2nW52XC4aSkUA  PZ-LZzSlhSe9utkQYU8pFg       3.1
39       8sdI6ez5FnEbhOiWSvaLVA  PZ-LZzSlhSe9utkQYU8pFg       2.2
40       xPySNt9FFPIfE07vcHJxPw  PZ-LZzSlhSe9utkQYU8pFg       5.1
41       co-GuD549dZTJ6OiJS1Ttw  KWywu2tTEPWmR9JnBc0WyQ       5.2
42       rzQyl74K5sDLUszXuogEEA  KWywu2tTEPWmR9JnBc0WyQ       5.2
43       2W12K5kX9uZglNqkJ4NjaQ  KWywu2tTEPWmR9JnBc0WyQ       2.4
44       p0IderpL5zE4D021CXVxtA  KWywu2tTEPWmR9JnBc0WyQ       5.2
45       5ziFur72HgbuvfaSXASdPQ  KWywu2tTEPWmR9JnBc0WyQ       5.2
46       iqXtduiWnTPW9A90mocp5Q  KWywu2tTEPWmR9JnBc0WyQ       5.2
47       wqRcCohnU8tXl91RySQFnQ  KWywu2tTEPWmR9JnBc0WyQ       1.6
48       eojKDDLxoB4aLw0AZdVKlg  KWywu2tTEPWmR9JnBc0WyQ       5.2
49       nWAsg9LsVpG7SSNz7vbqJA  KWywu2tTEPWmR9JnBc0WyQ       1.6
50       IbBze7C6KylGCdCDb7U9FA  KWywu2tTEPWmR9JnBc0WyQ       1.6
51       9nw8X4eYw1QlP55wAj8sIA  KWywu2tTEPWmR9JnBc0WyQ       5.2
52       cpoJZ8_c43W22pWHCNPCoA  KWywu2tTEPWmR9JnBc0WyQ       5.2
53       N4boE_V9Di5efdvJw5K3YQ  KWywu2tTEPWmR9JnBc0WyQ       5.2
54       iFnkxWfuAmvIeV8DoehLkw  KWywu2tTEPWmR9JnBc0WyQ       5.2
55       IildZ_8utjDm-0VE94_xbw  KWywu2tTEPWmR9JnBc0WyQ       5.2
56       xcBFJitTvDYPt7pO-aNTrg  KWywu2tTEPWmR9JnBc0WyQ       1.6
57       jF9z0D-WPrAPs1ItJm5d5g  KWywu2tTEPWmR9JnBc0WyQ       5.2
58       zTykmNRo_P3vhpLoY0KaXA  KWywu2tTEPWmR9JnBc0WyQ       5.2
59       w6u_2e2zj0-ALPL19_eopw  KWywu2tTEPWmR9JnBc0WyQ       5.

In [160]:
reader = Reader(rating_scale=(1, 7))#(rating_scale=(0, 9))
data = Dataset.load_from_df(df[["user_id","business_id","newStars"]], reader)

In [161]:
# test set is made of 25% of the ratings.
trainset1, testset1 = train_test_split(data, test_size=.25)


In [162]:
trainset1

In [163]:
testset1

[('f8PDt-178ZhiB4DQ3XpNYA', 'HhVmDybpU7L50Kb5A0jXTg', 5.9),
 ('j2wdX8VZ5nLXQkBErWMucg', '3BCsAgo_1i4xMuTyLKMLRQ', 5.25),
 ('5JrVWogzqxo6gnaEvlf8Sg', '5CJOaZc8Muu8WothauxQ4g', 1.25),
 ('ybJkYYEBvFGVb-or4i9_oA', 'U9aA5H13y7t9xWnoQslV0Q', 2.15),
 ('bF94vG4-iserSe-4rLLDtw', 'KaGZE0_o1EmmSN4Fo_cpUw', 5.4),
 ('_UL8s7ihJBRnHeWfziKeDQ', 'RESDUcs7fIiihp38-d6_6g', 3.6),
 ('IYErGJC5VV88th6H7uUTHQ', 'Kbnet8BjbZpXoR_q7JLZPA', 5.2),
 ('LVpB1OC4kEJUkJ4ppFLVYw', 'KVsv8wRGnLX8QWoNZKNMQA', 5.3),
 ('QhzzVcCXetK2hCctHsMzmg', 'y7Js-07RF8d3N_AEtaw2VQ', 4.4),
 ('5hglUCQ4syGEhZkOUEt55A', 'lsLelczQjIZLHVt2-e44lA', 5.4),
 ('qvQReEXcC3eTRt7lxz13Og', 'dYDuaXVyIXMXlmeMYf2ktw', 5.2),
 ('_BhEr249ouzfOnXv1G-CsA', 'VkECNTcZZ1mdN-VJltJcWA', 3.1),
 ('5zCt09hfkCiFW3q3RTnoaw', 'eAc9Vd6loOgRQolMXQt6FA', 2.2),
 ('lW9B0GUMNjjdmo7JU3vRWg', 'dWw7M_JsAVUprR86--89ZA', 4.1),
 ('4sbPjnH_uxMEaEvx2bU8xQ', 'cUHPc4rW6qi3yTBPdQDCKw', 1.2),
 ('8DBH3BpLINfTAK_Up5BtUQ', 'KalAJyO0Zpg3K1wVwYXBHA', 4.15),
 ('wtI03sa9H3hgjir_lEvscA', 'PChG1Dm

In [169]:
bsl_options = {'method': 'als',
               'n_epochs': 5,
               'reg_u': 10,
               'reg_i': 15
               }
algo = BaselineOnly(bsl_options=bsl_options)
cross_validate(algo, data, measures=['RMSE'], cv=3, verbose=True)

Estimating biases using als...
Estimating biases using als...
Estimating biases using als...
Evaluating RMSE of algorithm BaselineOnly on 3 split(s).

                  Fold 1  Fold 2  Fold 3  Mean    Std     
RMSE (testset)    nan     3.2208  3.2219  nan     nan     
Fit time          3.74    4.17    4.02    3.98    0.18    
Test time         4.58    4.36    4.29    4.41    0.12    


{'test_rmse': array([       nan, 3.22083305, 3.22189069]),
 'fit_time': (3.7351901531219482, 4.167101144790649, 4.023844003677368),
 'test_time': (4.576028823852539, 4.358501672744751, 4.292696952819824)}

In [172]:
## Using SGD
bsl_options = {'method': 'sgd',
               'learning_rate': 0.001 #.00005,
               }
algo = BaselineOnly(bsl_options=bsl_options,verbose=True)
cross_validate(algo, data, measures=['RMSE'], cv=3, verbose=False)

Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...


{'test_rmse': array([3.22090938, 3.21909275,        nan]),
 'fit_time': (7.431644916534424, 7.62769889831543, 7.757200241088867),
 'test_time': (2.7169699668884277, 4.1938371658325195, 4.207682132720947)}

In [173]:
# test traing & prediction 
predictions = algo.fit(trainset1).test(testset1)
accuracy.rmse(predictions)

Estimating biases using sgd...
RMSE: 3.2230


3.2230417409568606

In [175]:
predictions

[Prediction(uid='f8PDt-178ZhiB4DQ3XpNYA', iid='HhVmDybpU7L50Kb5A0jXTg', r_ui=5.9, est=7, details={'was_impossible': False}),
 Prediction(uid='j2wdX8VZ5nLXQkBErWMucg', iid='3BCsAgo_1i4xMuTyLKMLRQ', r_ui=5.25, est=7, details={'was_impossible': False}),
 Prediction(uid='5JrVWogzqxo6gnaEvlf8Sg', iid='5CJOaZc8Muu8WothauxQ4g', r_ui=1.25, est=7, details={'was_impossible': False}),
 Prediction(uid='ybJkYYEBvFGVb-or4i9_oA', iid='U9aA5H13y7t9xWnoQslV0Q', r_ui=2.15, est=7, details={'was_impossible': False}),
 Prediction(uid='bF94vG4-iserSe-4rLLDtw', iid='KaGZE0_o1EmmSN4Fo_cpUw', r_ui=5.4, est=7, details={'was_impossible': False}),
 Prediction(uid='_UL8s7ihJBRnHeWfziKeDQ', iid='RESDUcs7fIiihp38-d6_6g', r_ui=3.6, est=7, details={'was_impossible': False}),
 Prediction(uid='IYErGJC5VV88th6H7uUTHQ', iid='Kbnet8BjbZpXoR_q7JLZPA', r_ui=5.2, est=7, details={'was_impossible': False}),
 Prediction(uid='LVpB1OC4kEJUkJ4ppFLVYw', iid='KVsv8wRGnLX8QWoNZKNMQA', r_ui=5.3, est=7, details={'was_impossible': False}

In [166]:
## Using SGD
bsl_options = {'method': 'sgd',
               'learning_rate': 0.001 #.00005,
               }
algo = BaselineOnly(bsl_options=bsl_options,verbose=True)
cross_validate(algo, data, measures=['RMSE'], cv=3, verbose=False)

Estimating biases using sgd...
Estimating biases using sgd...


KeyboardInterrupt: 

In [ ]:
# test traing & prediction 
predictions = algo.fit(trainset1).test(testset1)
accuracy.rmse(predictions)